<a href="https://colab.research.google.com/github/danil-zhembrovskii/study_projects/blob/main/1_Lab_3_district.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install numpy==1.23.0  # какие-то проблемы с зависимостямя
!pip install geopandas mapclassify  # mapclassify для визуализации
!pip install keplergl  # для визуализации
!pip install osmnx  # устанавливаем модуль osmnx
!pip install shapely

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.0/17.0 MB 31.7 MB/s eta 0:00:00
  Attempting uninstall: numpy
    Found existing installation: numpy 1.23.1
    Uninstalling numpy-1.23.1:
      Successfully uninstalled numpy-1.23.1


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import osmnx as ox
import geopandas as gpd
from tqdm import tqdm
from shapely.geometry import Point
import numpy as np
import keplergl
from keplergl import KeplerGl

In [ ]:
from google.colab import output
output.enable_custom_widget_manager()

In [ ]:
# функция формирования границ территории разбиения на кварталы через запрос osm
def get_territory_gdf(territory_name):
    territory = ox.geocode_to_gdf(territory_name)
    return territory

# конвертация crs для корректного расчёта площади
def convert_crs(src_territory, new_crs: int, inplace = False):
    return src_territory.to_crs(new_crs, inplace = inplace)

# функция фильтрации по минимальной площади
def filter_min_area_districts(districts, ter_crs, min_area = 1000):
    districts['area'] = districts.to_crs(ter_crs).area
    districts = districts[districts['area']>=1000]
    return districts

In [ ]:
ter_name = 'Калининград'
ter_crs = 32636

territory = get_territory_gdf(ter_name)
metric_territory = convert_crs(territory, ter_crs)
metric_territory.crs

<Projected CRS: EPSG:32636>
Name: WGS 84 / UTM zone 36N
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: Between 30°E and 36°E, northern hemisphere between equator and 84°N, onshore and offshore. Belarus. Cyprus. Egypt. Ethiopia. Finland. Israel. Jordan. Kenya. Lebanon. Moldova. Norway. Russian Federation. Saudi Arabia. Sudan. Syria. Türkiye (Turkey). Uganda. Ukraine.
- bounds: (30.0, 0.0, 36.0, 84.0)
Coordinate Operation:
- name: UTM zone 36N
- method: Transverse Mercator
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [ ]:
map = KeplerGl(height = 500)
map.add_data(metric_territory.copy())
map

User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


KeplerGl(data={'unnamed': {'index': [0], 'columns': ['geometry', 'bbox_north', 'bbox_south', 'bbox_east', 'bbo…

In [ ]:
roads = ox.graph_to_gdfs(ox.graph_from_place(ter_name, network_type = 'drive'), nodes = False) # получаю граф автомобильных дорог без самих точек графа
roads.reset_index(drop=True, inplace=True)
map.add_data(roads.copy())
map

KeplerGl(config={'version': 'v1', 'config': {'visState': {'filters': [], 'layers': [{'id': 'dh9gq2h', 'type': …

In [ ]:
roads_buffered = roads.copy()
roads_buffered.geometry = convert_crs(roads_buffered, ter_crs).buffer(10) # создаю 5 метровый буфер вокруг дорог + задаю crs
map.add_data(roads_buffered.copy())
map

KeplerGl(config={'version': 'v1', 'config': {'visState': {'filters': [], 'layers': [{'id': 'dl6cvw', 'type': '…

In [ ]:
# дополнительно также удалю железнодорожные пути и всю сопутствующую инфраструктуру
tags = {'railway': True}  
railway = ox.geometries_from_polygon(territory.unary_union, tags)
railway = railway[railway.geometry.type=='LineString']  # выбираю только линии для дальнейшего создания буферных зон 
railway.reset_index(drop=True, inplace=True)
railway = railway[railway['railway']!='abandoned']  # без заброшенных/несуществующих жд

In [ ]:
railway_buffered = railway.copy()
railway_buffered.geometry = convert_crs(railway_buffered, ter_crs).buffer(5)
map.add_data(railway_buffered.copy())
map

KeplerGl(config={'version': 'v1', 'config': {'visState': {'filters': [], 'layers': [{'id': 'dh9gq2h', 'type': …

In [ ]:
tags = {'water': True, 'leisure': ['park', 'garden'], 'landuse': ['railway', 'grass']}    # Выделю территории водных объектов, зелёных насаждений (газоны), парки
not_use_territory = ox.geometries_from_polygon(territory.unary_union, tags)
map.add_data(not_use_territory.copy())
map

KeplerGl(config={'version': 'v1', 'config': {'visState': {'filters': [], 'layers': [{'id': 'dh9gq2h', 'type': …

In [ ]:
not_use_territory = not_use_territory[not_use_territory.geometry.type!='Point']
not_use_territory.reset_index(drop=True, inplace=True)

In [ ]:
convert_crs(territory, 4326, inplace=True)    # перевожу все слои к единой crs для корректных вычислений
convert_crs(roads_buffered, 4326, inplace=True)
convert_crs(not_use_territory, 4326, inplace=True)
convert_crs(railway_buffered, 4326, inplace=True)
districts = gpd.overlay(territory, roads_buffered, how = 'difference')     # сначала "вырезаю" слой с дорогами, затем с жд линиями, а затем с парками и водными объектами
districts_1 = gpd.overlay(districts, railway_buffered, how = 'difference')
districts_2 = gpd.overlay(districts_1, not_use_territory, how = 'difference')

/usr/local/lib/python3.10/dist-packages/geopandas/tools/overlay.py:365: DeprecationWarning: In a future version, `df.iloc[:, i] = newvals` will attempt to set the values inplace instead of always setting a new array. To retain the old behavior, use either `df[df.columns[i]] = newvals` or, if columns are non-unique, `df.isetitem(i, newvals)`
  result.loc[is_collection, geom_col] = dissolved[geom_col].values
<ipython-input-33-73d7b43c0f10>:7: UserWarning: `keep_geom_type=True` in overlay resulted in 1916 dropped geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
  districts_2 = gpd.overlay(districts_1, not_use_territory, how = 'difference')


In [ ]:
map.add_data(districts_2.copy())
map

KeplerGl(config={'version': 'v1', 'config': {'visState': {'filters': [], 'layers': [{'id': 'dh9gq2h', 'type': …

In [ ]:
districts_splitted = districts_2.explode(ignore_index = True)   # разделение на кварталы
districts_splitted = filter_min_area_districts(districts_splitted, ter_crs, min_area = 1000)    
# фильтрую по минимальной площади. Отфильтровалось более 500 кварталов, что особенно заметно в районах промышленной застройки, где были ликвидированы кварталы между путями

In [ ]:
map.add_data(districts_splitted.copy())
map

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


KeplerGl(config={'version': 'v1', 'config': {'visState': {'filters': [], 'layers': [{'id': 'dh9gq2h', 'type': …